In [2]:
import sys
path2cpp_pkg = "/Users/mariusmahiout/Documents/repos/ising_core/build"
sys.path.append(path2cpp_pkg)
import ising

import os
os.chdir("/Users/mariusmahiout/Documents/repos/ising_core/python")
import src.preprocessing as pre
import src.model_eval as eval
import src.utils as utils
import src.misc_plotting as misc_plotting
import src.isingfitter as fitter
os.chdir("..")

import numpy as np
import matplotlib.pyplot as plt
import plotly
from plotly.subplots import make_subplots
import plotly.graph_objs as go
from IPython.display import display, HTML
from ipywidgets import HBox, VBox, widgets

plotly.offline.init_notebook_mode()
display(HTML(
    '<script type="text/javascript" async src="https://cdnjs.cloudflare.com/ajax/libs/mathjax/2.7.1/MathJax.js?config=TeX-MML-AM_SVG"></script>'
))

In [21]:
mouse_name = "Angie"
sens_param = "time"
sample_names = ["performing1", "performing2", "observing1", "observing2"]
path = "analyses"
utils.make_dir(path)

bin_widths = [50, 150, 250]
labels = [str(bin_width) + " ms" for bin_width in bin_widths]

num_units = 100
# M2, mouse Angie
# perfomring
samples1 = [pre.get_recording_sample(fname="RESULTS_Angie_20170825_1220_allbeh_1000s.mat", mouse_name=mouse_name, bin_width=bin_width, num_units=num_units) for bin_width in bin_widths]
samples2 = [pre.get_recording_sample(fname="RESULTS_Angie_20170825_1232_allbeh_1000s.mat", mouse_name=mouse_name, bin_width=bin_width, num_units=num_units) for bin_width in bin_widths]

# observing
samples3 = [pre.get_recording_sample(fname="RESULTS_Angie_20170825_1248_allbeh_1000s.mat", mouse_name=mouse_name, bin_width=bin_width, num_units=num_units) for bin_width in bin_widths]
samples4 = [pre.get_recording_sample(fname="RESULTS_Angie_20170825_1158_allbeh_1000s.mat", mouse_name=mouse_name, bin_width=bin_width, num_units=num_units) for bin_width in bin_widths]

Directory 'analyses' already exists.


In [22]:
sample = samples1[2]

In [23]:
num_sims = 50_000
num_burn = 5000
lr = 0.1
win_size = 10
tol_ml = 1e-3
tol_pl = 1e-9
max_steps = 5000

In [24]:
###############
# EQUILIBRIUM #
###############

# setting up model
h_init = np.random.uniform(-1.5, 1.5, num_units)
J_init = np.random.normal(0,  1,  (num_units, num_units))
J_init = (J_init.T + J_init) * np.sqrt(2) / 2
np.fill_diagonal(J_init, 0)

eq_model = ising.EqModel(J_init, h_init)

eq_fitter = fitter.EqFitter(eq_model)
eq_fitter.TAP(sample)

# inference
use_llh = False
eq_fitter.maximize_likelihood(
        sample=sample, 
        max_steps=max_steps, 
        learning_rate=0.075,
        win_size = win_size,
        tolerance= tol_ml, 
        num_sims=30_000, 
        num_burn=5_000,
        calc_llh=False
)

In [25]:
###################
# NON-EQUILIBRIUM #
###################

# setting up model
h_init = np.random.uniform(-1.5, 1.5, num_units)
J_init = np.random.normal(0,  1,  (num_units, num_units))
J_init = (J_init.T + J_init) * np.sqrt(2) / 2
np.fill_diagonal(J_init, 0)

neq_model = ising.NeqModel(J_init, h_init)

neq_fitter = fitter.NeqFitter(neq_model)
neq_fitter.TAP(sample)

# inference
use_llh = False
neq_fitter.maximize_likelihood(
    sample=sample, 
    max_steps=5000, 
    learning_rate=0.075,
    win_size = win_size,
    tolerance= 1e-16, 
)

In [26]:
misc_plotting.convergence_plot(eq_fitter, plot_llh=False, path="./analyses/eq_convergence/pllh1.pdf")

Button(description='Save Figure', style=ButtonStyle())

In [27]:
eq_sim = eq_model.simulate(num_sims, num_burn)
neq_sim = neq_model.simulate(num_sims, num_burn)

In [28]:


labels = ["EQ", "NEQ"]
metadata = utils.get_metadata( # gotta change this
    num_units=num_units,
    is_empirical_analysis=False,
    eq_inv_methods=labels,
    num_sims=num_sims,
    true_fields="Angie performing 1",
    true_couplings="Angie performing 1",
    num_steps=max_steps,
    learning_rate=lr,
    is_converged=None,
    num_sims_ml=num_sims,
    num_burn_ml=num_burn,
)


analysis_name = "rec_test"
bin_width = 0
analysis_path = utils.get_analysis_path(analysis_name, num_units, bin_width)

layout_spec = {
    ("means", "scatter"): (1, 1),
    ("ccorrs", "scatter"): (1, 2),
    ("dcorrs", "scatter"): (2, 1),    
    ("tricorrs", "scatter"): (2, 2),    
}

ising_eval = eval.IsingEval(
    analysis_path=analysis_path,
    metadata=metadata,
    true_model=None,
    est_models=[eq_model, neq_model],#
    true_sample=sample,
    est_samples=[eq_sim, neq_sim],#],#
    labels=labels,
    layout_spec=layout_spec
)
ising_eval.generate_plots()

    'data': [{'legendgroup': 'EQ',
              'marker': {'color': 'blue', 'si…

Directory './analyses/./n100b0rec_test/' was created.
Directory './analyses/./n100b0rec_test/figures/' was created.
Directory './analyses/./n100b0rec_test/' already exists.
Directory './analyses/./n100b0rec_test/figures/' already exists.
